# ATAC-Seq data analysis

**Authors** - Jayadev Joshi, Daniel Blankenberg.<br>
**Contact Email** - jayadev.joshi12@gmail.com

# Table of Contents
<a href=#1.-Introduction>Introduction</a>  
<a href=#2.-Login>Login to GenePattern</a>   
<a href=#3.-Preprocessing>Preprocessing</a>   
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#A.-Get-Data>Get Data</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#B.-Quality-Control>Quality Control</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#C.-Trimming-Reads>Trimming-Reads</a>   
<a href=#4.-Mapping>Mapping</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#A.-Mapping-reads-to-reference-genome>Mapping reads to reference genome</a>   
<a href=#5.-Filtering>Filtering</a>   
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#A.-Filter-Uninformative-Reads>Filter Uninformative Reads</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#B.-Filter-Duplicate-Reads>Filter Duplicate Reads</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#C.-Check-Insert-Size>Check Insert Size</a>  
<a href=#6.-Peak-calling>Peak calling</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#A.-Call-Peaks>Call Peaks</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#Cell-Type-Identification-with-CoGAPS>Cell Type Identification with CoGAPS</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#Exploring-the-Patterns>Exploring the Patterns</a>   
<a href=#7.-Visualisation-of-Coverage>Visualisation of Coverage</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#A.-Prepare-the-Datasets>Prepare the Datasets</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#B.-Create-heatmap-of-coverage-at-TSS-with-deepTools>Create heatmap of coverage at TSS with deepTools</a>  
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;<a href=#C.-Visualise-Regions-with-pyGenomeTracks>Visualise Regions with pyGenomeTracks</a>  
<a href=#8.-Conclusion>Conclusion</a>  
<a href=#9.-References>References</a> 

# 1. Introduction
The goal of this notebook is to provide an introduction to the general principles of ATAC-Seq data analysis. ATAC-Seq is a method to investigate chromatin accessibility and the genome is treated with a transposase (enzyme) called Tn5. It marks open chromatin regions by cutting and inserting adapters for sequencing. This tutorial notebook will provide you an insight into how to quality control the data. You will look for low-quality bases, adapter contamination, correct insert size, and PCR duplicates (duplication level). Further, we will learn how to remove adapters and PCR duplicates, if FastQC, shows a warning in these areas. We will map the reads with Bowtie2, filter our reads for properly paired, good-quality, and reads that do not map to the mitochondrial genome. We will search open chromatin regions with MACS2, a tool to find regions of genomic enrichment (peaks). We will investigate the read coverage around TSS with the help of computeMatrix and plotHeatmap. Last but not least, we will learn visualization of the peaks and other informative tracks, such as CTCF binding regions and hg38 genes, with the help of pyGenomeTracks. 

#### Analysis Overview
![scRNAseq_flow_diagram.png](https://training.galaxyproject.org/training-material/topics/epigenetics/images/atac-seq/ATACWF.svg)

**Figure 1: ATAC workflow.**(Source: [GTN tutorial](https://training.galaxyproject.org/training-material/topics/epigenetics/tutorials/atac-seq/tutorial.html))

# 2. Login 

Make sure to login here before proceeding any farther in the notebook. The module output won't appear until you are logged in.

In [ ]:
import GiN.authwidget
import nbtools

nbtools.tool(id='galaxy_authentication', origin='+')

GalaxyAuthWidget(buttons={'Register an Account': ''}, color='#2c3143', description='Login to Galaxy instance b…

# 3. Preprocessing

### A. Get Data

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li><b>Initial data:</b> You can get initial data either through the zenodo link below, or you can upload your data files to the Galaxy server using GiN's Data Upload tool.</li></ol>
   
     https://zenodo.org/record/3862793/files/ENCFF933NTR.bed.gz
     https://zenodo.org/record/3862793/files/SRR891268_chr22_enriched_R1.fastq.gz
     https://zenodo.org/record/3862793/files/SRR891268_chr22_enriched_R2.fastq.gz
    


<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
<ol><li><b>Obtain Annotation for hg38 genes: </b> We will visualize regions later in the analysis and obtain the gene information now. Information for chromosome 22 genes (names of transcripts and genomic positions) were obtained using the UCSC Browser and dowload fromt the link below.</li></ol>

> [**Chromosome 22 genes**](https://protect-us.mimecast.com/s/r9mfCn5XvWuX14yk7H9-lbF?domain=datasets.genepattern.org):

 <li> <b>Gene file: </b>This table contains all the information but is not in a BED format. To transform it into BED format we will cut out the required columns and rearrange:</li>
    </ol>


### Hands-on:  **Cut columns** from a table with the following parameters:

> - **1.** **Cut columns**: `c3,c5,c6,c13,c12,c4` 
> - **2.** **Delimited by**: `Tab` 
> - **3.** **From**: `UCSC Main on Human: wgEncodeGencodeBasicV31 (chr22:1-50,818,468)` 

- Check the contents of your file, is this as you expect it to be?

> - **1.** **Rename** the dataset as `chr22 genes` by clicking the pencile icon  
> - **2.** **Change** its datatype to BED by clicking the pencile icon 
    
</div>
    


In [14]:
nbtools.tool(id='Cut1', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='columns from a table', galaxy_tool_id='Cut1', history_data=[{'i…

### B. Quality Control


<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
<ol><li>The first step is to check the quality of the reads and the presence of the Nextera adapters. When we perform ATAC-Seq, we can get DNA fragments of about 40 bp if two adjacent Tn5 transposases cut the DNA. This can be smaller than the sequencing length so we expect to have Nextera adapters at the end of those reads. We can assess the reads with <b>FastQC</b>.</li></ol>


### Hands-on: Quality Control with **FastQC**

> - **1.** **FastQC**  with the following parameters:
>    - **Short read data from your current history**: Choose here either only the `SRR891268_R1` file with or use  **Multiple datasets** to choose both `SRR891268_R1` and `SRR891268_R2`.
> - **2.** Inspect the web page output of **FastQC** for the `SRR891268_R1` sample. Check what adapters are found at the end of the reads.
    
</div>

In [12]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/devteam/fastqc/fastqc/0.73+galaxy0', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='Read Quality reports', galaxy_tool_id='toolshed.g2.bx.psu.edu/r…

### C. Trimming Reads


<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li>To trim the adapters we provide the Nextera adapter sequences to <b>Cutadapt</b>. The forward and reverse adapters are slightly different. We will also trim low quality bases at the ends of the reads (quality less than 20). We will only keep reads that are at least 20 bases long. We remove short reads (< 20bp) as they are not useful, they will either be thrown out by the mapping or may interfere with our results at the end. </li></ol>



 ### Hands-on: **Cutadapt** with the following parameters:
>   - **1.** **Single-end or Paired-end reads?**: `Paired-end` 
>        - **FASTQ/A file #1**: select `SRR891268_R1`  
>        - **FASTQ/A file #2**: select `SRR891268_R2` 
>        - In **Read 1 Options**:  
>            - In **3' (End) Adapters**:  
>                -  **Insert 3' (End) Adapters**  
>                    - **Source**: `Enter custom sequence`  
>                        -  **Enter custom 3' adapter name (Optional if Multiple output is 'No')**: `Nextera R1`  
>                        -  **Enter custom 3' adapter sequence**: `CTGTCTCTTATACACATCTCCGAGCCCACGAGAC`  
>        - In **Read 2 Options**:  
>            - In **3' (End) Adapters**:  
>                -  **Insert 3' (End) Adapters**  
>                    - **Source**: `Enter custom sequence` 
>                        -  **Enter custom 3' adapter name (Optional)**: `Nextera R2`  
>                        -  **Enter custom 3' adapter sequence**: `CTGTCTCTTATACACATCTGACGCTGCCGACGA`  
>   - **2.** In **Filter Options**:  
>        -  **Minimum length**: `20`  
>   - **3.** In **Read Modification Options**: 
>        -  **Quality cutoff**: `20`  
>   - **4.** In **Output Options**: 
>        - **Report**: `Yes`
>  - **5.**  Click on the  (eye) icon of the report and read the first lines. 
    
</div>


In [4]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/lparsons/cutadapt/cutadapt/4.0+galaxy1', origin='https://usegalaxy.org')

NameError: name 'nbtools' is not defined

###  Cutadapt Results
You should get similar output to this from Cutadapt:

> ![Summary of cutadapt](https://training.galaxyproject.org/training-material/topics/epigenetics/images/atac-seq/Screenshot_cutadaptSummary.png)

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li><b>FastQC on the trimmed data: </b> Run <b>FastQC</b> again to check the quality of the reads after treamming the reads.</li></ol>


###  Hands-on: Check Adapter Removal with FastQC

> - **1.** **FastQC** with the default parameters
>    - **Short read data from your current history** select the output of **Cutadapt**  **Multiple datasets** to choose both `Read 1 Output` and `Read 2 Output`.
> - **2.** Click on the  (eye) icon of the report and read the first lines.
    
</div>

In [6]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/devteam/fastqc/fastqc/0.73+galaxy0', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='Read Quality reports', galaxy_tool_id='toolshed.g2.bx.psu.edu/r…

## 4. Mapping

### A. Mapping reads to reference genome

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li>Next we map the trimmed reads to the human reference genome. Here we will use <b>Bowtie2</b>. We will extend the maximum fragment length (distance between read pairs) from 500 to 1000 because we know some valid read pairs are from this fragment length. We will use the <b>--very-sensitive</b> parameter to have more chance to get the best match even if it takes a bit longer to run. We will run the end-to-end mode because we trimmed the adapters so we expect the whole read to map, no clipping of ends is needed. Regarding the genome to choose. The hg38 version of the human genome contains alternate loci. This means that some region of the genome are present both in the canonical chromosome and on its alternate loci. The reads that map to these regions would map twice. To be able to filter reads falling into repetitive regions but keep reads falling into regions present in alternate loci, we will map on the Canonical version of <b>hg38</b> (only the chromosome with numbers, chrX, chrY, and chrM).</li></ol>


>
### Hands-on: **Bowtie2** with the following parameters:

>
>    - **1.** **Is this single or paired library**: `Paired-end`
>        - **FASTQ/A file #1**: select the output of **Cutadapt** **Read 1 Output**
>        - **FASTQ/A file #2**: select the output of **Cutadapt** **Read 2 Output**
>        - **Do you want to set paired-end options?**: `Yes`
>            - **Set the maximum fragment length for valid paired-end alignments**: `1000`
>            - **Allow mate dovetailing**: `Yes`
>    - **2.** **Will you select a reference genome from your history or use a built-in index?**: `Use a built-in genome index`
>        - **Select reference genome**: `Human (Homo sapiens): hg38 Canonical`
>    - **3.** **Select analysis mode**: `1: Default setting only`
>        - **Do you want to use presets?**: `Very sensitive end-to-end (--very-sensitive)`
>    - **4.** **Save the bowtie2 mapping statistics to the history**: `Yes`
>
> - **5.**  Click on the (eye) icon of the mapping stats.


### Bowtie2 Results

You should get similar results to this from Bowtie2:

![Mapping statistics of bowtie2](https://training.galaxyproject.org/training-material/topics/epigenetics/images/atac-seq/Screenshot_bowtie2MappingStats.png)

**Figure 6:** Mapping statistics of bowtie2
    
</div>

In [69]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/devteam/bowtie2/bowtie2/2.5.0+galaxy0', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='- map reads against reference genome', galaxy_tool_id='toolshed…

## 5. Filtering 

### A. Filter Uninformative Reads


<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
<ol><li>We apply some filters to the reads after the mapping. ATAC-Seq datasets can have a lot of reads that map to the mitchondrial genome because it is nucleosome-free and thus very accessible to Tn5 insertion. The mitchondrial genome is uninteresting for ATAC-Seq so we remove these reads. We also remove reads with low mapping quality and reads that are not properly paired..</li></ol>


### Hands-on: **Filter** BAM datasets on a variety of attributeswith the following parameters:
>    - **1.** **BAM dataset(s) to filter**: Select the output of  **Bowtie2**  **alignments**
>    - **2.**  In **Condition**
>         - **1: Condition**
>            - In **Filter**:
>                - **1: Filter**
>                    - **Select BAM property to filter on**: `mapQuality`
>                        - **Filter on read mapping quality (phred scale)**: `>=30`
>                - **Insert Filter**
>                    - **Select BAM property to filter on**: `isProperPair`
>                        - **Select properly paired reads**: `Yes`
>                - **Insert Filter**
>                    - **Select BAM property to filter on**: `reference`
>                        - **Filter on the reference name for the read**: `!chrM`
>    - **3.** **Would you like to set rules?**: `No`
>
> - **4.** Click on the input and the output BAM files of the filtering step. Check the size of the files.
    
High numbers of mitochondrial reads can be a problem in ATAC-Seq. Some ATAC-Seq samples have been reported to be 80% mitochondrial reads and so wet-lab methods have been developed to deal with this issue. It can be a useful QC to assess the number of mitochondrial reads.
    
</div>

In [6]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/devteam/bamtools_filter/bamFilter/2.5.2+galaxy1', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='datasets on a variety of attributes', galaxy_tool_id='toolshed.…

### B. Filter Duplicate Reads


<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
<ol><li>Because of the PCR amplification, there might be read duplicates (different reads mapping to exactly the same genomic region) from overamplification of some regions. As the Tn5 insertion is random within an accessible region, we do not expect to see fragments with the same coordinates. We consider such fragments to be PCR duplicates. We will remove them with <b>Picard MarkDuplicates</b>.</li></ol>


 
### Hands-on: Remove duplicates
> 1. **MarkDuplicates** with the following parameters:
>    -  **Select SAM/BAM dataset or dataset collection**: Select the output of  **Filter**  **BAM**
>    -  **If true do not write duplicates to the output file instead of writing them with appropriate flags set**: `Yes`
>

<ol><li>By default, the tool will only "Mark" the duplicates. This means that it will change the Flag of the duplicated reads to enable them to be filtered afterwards. We use the parameter *"If true do not write duplicates to the output file instead of writing them with appropriate flags set"* to directly remove the duplicates. </li></ol>


> - **1.** Click on the (eye) icon of the MarkDuplicate metrics.

![Metrics of MarkDuplicates](https://training.galaxyproject.org/training-material/topics/epigenetics/images/atac-seq/Screenshot_picardRemoveDup.png)

**Figure 8:** Metrics of MarkDuplicates

</div>

In [6]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/devteam/picard/picard_MarkDuplicates/2.18.2.3', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='examine aligned records in BAM datasets to locate duplicate mol…

### C. Check Insert Size

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li>We will check the insert sizes with <b>Picard CollectInsertSizeMetrics</b>. The insert size is the distance between the R1 and R2 read pairs. This tells us the size of the DNA fragment the read pairs came from. The fragment length distribution of a sample gives a very good indication of the quality of the ATAC-Seq.</li></ol>


### Hands-on: **Paired-end histogram** with the following parameters:

> - **1.** **BAM file**: Select the output of  **MarkDuplicates** **BAM output**
> - **2.** **Lower bp limit (optional)**: `0`
> - **3.** **Upper bp limit (optional)**: `1000`
> - **4.** Click on the (eye) icon of the lower one of the 2 outputs (the png file).
</div>

In [39]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/iuc/pe_histogram/pe_histogram/1.0.1', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='of insert size frequency', galaxy_tool_id='toolshed.g2.bx.psu.e…

## 6. Peak calling

### A. Call Peaks


<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
<ol><li>We have now finished the data preprocessing. Next, in order to find regions corresponding to potential open chromatin regions, we want to identify regions where reads have piled up (peaks) greater than the background read coverage.</li>
    <li>We convert the BAM file to BED format because when we set the extension size in MACS2, it will only consider one read of the pair while here we would like to use the information from both.</li> 
    </ol>


### Hands on: **bedtools BAM to BED** tool Converts the BAM to BED
>
> - **1.** [bedtools BAM to BED converter](toolshed.g2.bx.psu.edu/repos/iuc/bedtools/bedtools_bamtobed/2.30.0) with the following parameters:
>    -  **Convert the following BAM file to BED**: Select the output of **MarkDuplicates** 
>
</div>

In [17]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/iuc/bedtools/bedtools_bamtobed/2.30.0+galaxy2', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='converter', galaxy_tool_id='toolshed.g2.bx.psu.edu/repos/iuc/be…

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li><b>Call peaks with MACS2: </b>We call peaks with MACS2. In order to get the coverage centered on the 5' extended 100bp each side we will use <b>--shift 100</b> and <b>--extend 200</b>.</li></ol>



### Hands on: **MACS2 callpeak** with the following parameters:
>    - **1.** **Are you pooling Treatment Files?**: `No`
>        - Select the output of **bedtools BAM to BED** converter
>    - **2.** **Do you have a Control File?**: `No`
>    - **3.** **Format of Input Files**: `Single-end BED`
>    - **4.** **Effective genome size**: `H. sapiens (2.7e9)`
>    - **5.** **Build Model**: `Do not build the shifting model (--nomodel)`
>        - **Set extension size**: `200`
>        - **Set shift size**: `-100`. It needs to be - half the extension size to be centered on the 5'.
>    - **6.** **Additional Outputs**:
>        - Check `Peaks as tabular file (compatible with MultiQC)`
>        - Check `Peak summits`
>        - Check `Scores in bedGraph files`
>    - **7.** In **Advanced Options**:
>        - **Composite broad regions**: `No broad regions`
>            - **Use a more sophisticated signal processing approach to find subpeak summits in each enriched peak region**: `Yes`
>        - **How many duplicate tags at the exact same location are allowed?**: `all`
>
    
</div>

In [30]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/iuc/macs2/macs2_callpeak/2.2.7.1+galaxy0', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='Call peaks from alignment results', galaxy_tool_id='toolshed.g2…

## 7. Visualisation of Coverage

### A. Prepare the Datasets

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
<ol><li><b>Extract CTCF peaks on chr22 in intergenic regions: </b> As our training dataset is focused on chromosome 22 we will only use the CTCF peaks from chr22. We expect to have ATAC-seq coverage at TSS but only good ATAC-seq have coverage on intergenic CTCF. Indeed, the CTCF protein is able to position nucleosomes and creates a region depleted of nucleosome of around 120bp. This is smaller than the 200bp nucleosome-free region around TSS and also probably not present in all cells. Thus it is more difficult to get enrichment. In order to get the list of intergenic CTCF peaks of chr22, we will first select the peaks on chr22 and then exclude the one which overlap with genes.</li></ol>


### Hands on: Select CTCF peaks from chr22 in intergenic regions
>
> - **1.** Filter data on any column using simple expressions (Filter1) with the following parameters:
>    -  **Filter**: Select the first dataset: `ENCFF933NTR.bed.gz`
>    -  **With following condition**: `c1=='chr22'`
    
</div>

In [37]:
nbtools.tool(id='Filter1', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='data on any column using simple expressions', galaxy_tool_id='F…

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>

### Hands-on: **bedtools Intersect intervals find overlapping intervals in various ways** with the following parameters:
>    - **1.**  **File A to intersect with B**: Select the output of **Filter** data on any column using simple expressions
>    - **2.** **Combined or separate output files**: `One output file per 'input B' file`
>        -  **File B to intersect with A**:  Select the dataset `chr22 genes`
>    - **3.** **What should be written to the output file?**: `Write the original entry in A for each overlap (-wa)`
>    - **4.** **Required overlap**: `Default: 1bp`
>    - **5.** **Report only those alignments that **do not** overlap with file(s) B**: `Yes`
>    - **6.**  Rename the datasets `intergenic CTCF peaks chr22`.
    
</div>

In [46]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/iuc/bedtools/bedtools_intersectbed/2.30.0+galaxy1', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='find overlapping intervals in various ways', galaxy_tool_id='to…

### Convert bedgraph from **MACS2** to bigwig
<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li> <b>Convert bedgraph from MACS2 to bigwig: </b> The bedgraph format is easily readable for human but it can be very large and visualising a specific region is quite slow. We will change it to bigwig format which is a binary format, so we can visualise any region of the genome very quickly. In this tutorial we focus on chr22, thus we could restrict our bedgraph to chr22 before doing the conversion. This will both speed-up the conversion and decrease the amount of memory needed.</li></ol>


### Hands-on: **Filter** data on any column using simple expressions with the following parameters:
> - **1.** **Filter**: Select the output of **MACS2** (Bedgraph Treatment).
> - **2.** **With following condition**: `c1=='chr22'`

- This will decrease by half the size of the file.
In the next step, choose the output of **Filter** instead of the output of **MACS2**.


    **Wig/BedGraph-to-bigWig** with the following parameters:
>    - **1.** **Convert**: Select the output of **MACS2** (Bedgraph Treatment).
>    - **2.** **Converter settings to use**: `Default`
>    - **3.** Rename the datasets `MACS2 bigwig`.
</div>

In [53]:
nbtools.tool(id='wig_to_bigWig', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='converter', galaxy_tool_id='wig_to_bigWig', history_data=[{'id'…

### B. Create heatmap of coverage at TSS with deepTools


<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
<ol><li> We will use the <b>deepTools plotHeatmap</b> to check the coverage on specific regions. As an example, we will here make a heatmap centered on the transcription start sites (TSS) and another one centered on intergenic CTCF peaks. First, on the TSS.</li>
    <li><b>Generate computeMatrix: </b> The input of plotHeatmap is a matrix in a hdf5 format. To generate it we use the tool computeMatrix that will evaluate the coverage at each locus we are interested in.</li></ol>    


### Hands-on  **computeMatrix** with the following parameters:
>    - **1.** In **Select regions**:
>        -  **Insert Select regions**
>            -  **Regions to plot**: Select the dataset `chr22 genes`
>    - **2.** **Sample order matters**: `No`
>        - **Score file**: Select the output of **Wig/BedGraph-to-bigWig** that should be named `MACS2 bigwig`.
>    - **3.** **computeMatrix has two main output options**: `reference-point`
>    - **4.** **The reference point for the plotting**: `beginning of region (e.g. TSS)`
>    - **5.** **Show advanced output settings**: `no`
>    - **6.** **Show advanced options**: `yes`
>         - **Convert missing values to 0?**: `Yes`
>
</div>

In [59]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/bgruening/deeptools_compute_matrix/deeptools_compute_matrix/3.5.1.0.0', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='prepares data for plotting a heatmap or a profile of given regi…



<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li> <b>Plot with plotHeatmap: </b> We will now generate a heatmap. Each line will be a transcript. The coverage will be summarized with a color code from red (no coverage) to blue (maximum coverage). All TSS will be aligned in the middle of the figure and only the 2 kb around the TSS will be displayed. Another plot, on top of the heatmap, will show the mean signal at the TSS. There will be one heatmap per bigwig.</li></ol>


### Hands-on: **plotHeatmap** with the following parameters:
>    - **1.** **Matrix file from the computeMatrix tool**: Select the output of **computeMatrix**.
>    - **2.** **Show advanced output settings**: `no`
>    - **3.** **Show advanced options**: `no`

</div>

In [66]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/bgruening/deeptools_plot_heatmap/deeptools_plot_heatmap/3.5.1.0.1', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='creates a heatmap for score distributions across genomic region…

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
<ol><li>Now we will repeat the procedure for CTCF peaks of chr22 in intergenic regions.</li></ol>

### Hands-on: **computeMatrix** with the following parameters:
>    - **1.** In **Select regions**:
>        -  **Insert Select regions**
>            -  **Regions to plot**: Select the dataset `intergenic CTCF peaks chr22`
>    - **2.** **Sample order matters**: `No`
>        -  **Score file**: Select the output of **Wig/BedGraph-to-bigWig**  that should be named `MACS2 bigwig`.
>    - **3.** **Would you like custom sample labels?**: `No, use sample names in the history`
>    - **4.** **computeMatrix has two main output options**: `reference-point`
>        - **The reference point for the plotting**: `center of region`
>    - **5.** **Show advanced output settings**: `no`
>    - **6.** **Show advanced options**: `yes`
>        - **Convert missing values to 0?**: `Yes`
</div>

In [73]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/bgruening/deeptools_compute_matrix/deeptools_compute_matrix/3.5.1.0.0', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='prepares data for plotting a heatmap or a profile of given regi…

<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    
<ol><li>We will use output of <b>computeMatrix</b> to plot heatmap.</li></ol>
    
### Hands-on:  **plotHeatmap** with the following parameters:
>    - **1.** **Matrix file from the computeMatrix tool**:  Select the output of **computeMatrix** .
>    - **2.** **Show advanced output settings**: `no`
>    - **3.** **Show advanced options**: `yes`
>        - In **Colormap to use for each sample**:
>            - **Insert Colormap to use for each sample**
>                - **Color map to use for the heatmap**: `Blues` # Or what you want
>        - **The x-axis label**: `distance from peak center (bp)`
>        - **The y-axis label for the top panel**: `CTCF peaks`
>        - **Reference point label**: `peak center`
>        - **Labels for the regions plotted in the heatmap**: `CTCF_peaks`
>        - **Did you compute the matrix with more than one groups of regions?**: `Yes, I used multiple groups of regions`
</div>

In [80]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/bgruening/deeptools_plot_heatmap/deeptools_plot_heatmap/3.5.1.0.1', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='creates a heatmap for score distributions across genomic region…

### C. Visualise Regions with pyGenomeTracks


<div class="alert alert-info">
<h3 style="margin-top: 0;">Instructions <i class="fa fa-info-circle"></i></h3>
    <ol><li>In order to visualise a specific region (e.g. the gene <b>RAC2</b>), we can either use a genome browser like <b>IGV</b> or <b>UCSC browser</b>, or use <b>pyGenomeTracks</b> to make publishable figures. We will use <b>pyGenomeTracks</b>.</li></ol>



### Hands-on: **pygenometracks** with the following parameters:
>    - **1.** **Region of the genome to limit the operation**: `chr22:37,193,000-37,252,000`
>    - **2.** In **Include tracks in your plot**:
>        -  **Insert Include tracks in your plot**
>            - **Choose style of the track**: `Bigwig track`
>                - **Plot title**: `Coverage from MACS2 (extended +/-100bp)`
>                - **Track file(s) bigwig format**: Select the output of **Wig/BedGraph-to-bigWig** called `MACS2 bigwig`.
>                - **Color of track**: Select the color of your choice
>                - **Minimum value**: `0`
>                - **height**: `5`
>                - **Show visualization of data range**: `Yes`
>        -  **Insert Include tracks in your plot**
>            - **Choose style of the track**: `NarrowPeak track`
>                - **Plot title**: `Peaks from MACS2 (extended +/-100bp)`
>                - **Track file(s) encodepeak or bed format**: Select the output of **MACS2** (narrow Peaks).
>                - **Color of track**: Select the color of your choice
>                - **display to use**: `box: Draw a box`
>                - **Plot labels (name, p-val, q-val)**: `No`
>        - **Insert Include tracks in your plot**
>            - **Choose style of the track**: `Gene track / Bed track`
>                - **Plot title**: `Genes`
>                - **Track file(s) bed or gtf format**: `chr22 genes`
>                - **Color of track**: Select the color of your choice
>                - **height**: `5`
>                - **Plot labels**: `yes`
>                    - **Put all labels inside the plotted region**: `Yes`
>                    - **Allow to put labels in the right margin**: `Yes`
>        - **Insert Include tracks in your plot**
>            - **Choose style of the track**: `NarrowPeak track`
>                - **Plot title**: `CTCF peaks`
>                - **Track file(s) encodepeak or bed format**: Select the first dataset: `ENCFF933NTR.bed.gz`
>                - **Color of track**: Select the color of your choice
>                - **display to use**: `box: Draw a box`
>                - **Plot labels (name, p-val, q-val)**: `No`
>        - **Insert Include tracks in your plot**
>            - **Choose style of the track**: `X-axis`
>
>    - **3.** Click on the (eye) icon of the output.
>


As CTCF creates accessible regions, a region containing a peak with no corresponding CTCF peak or TSS could be a putative enhancer. In the pyGenomeTracks plot we see a region like this located in the intron of a gene and another one between genes. However, it is impossible to guess from the position which would be the gene controlled by this region. And of course, more analyses are needed to assess if it is a real enhancer, for example, histone ChIP-seq, 3D structure, transgenic assay, etc.
    
</div>

In [92]:
nbtools.tool(id='toolshed.g2.bx.psu.edu/repos/iuc/pygenometracks/pygenomeTracks/3.8+galaxy0', origin='https://usegalaxy.org')

GalaxyTaskWidget(color='#2c3143', description='plot genomic data tracks', galaxy_tool_id='toolshed.g2.bx.psu.e…

### 8. Conclusion


This tutorial notebook  we learned how to perfome quality control, remove adapters and PCR duplicates. Further, we learned mapping of reads using Bowtie2.  filter our reads for properly paired, good-quality, and reads that do not map to the mitochondrial genome. We will search open chromatin regions with MACS2, a tool to find regions of genomic enrichment (peaks). We will investigate the read coverage around TSS with the help of computeMatrix and plotHeatmap. Last but not least, we will learn visualization of the peaks and other informative tracks, such as CTCF binding regions and hg38 genes, with the help of pyGenomeTracks.


In this tutorial, we have learned how to access data, execute tools and visualize data using GiN for ATAC-seq data analysis.  

### 9. References


- ***Lucille Delisle, Maria Doyle, Florian Heyl,*** ATAC-Seq data analysis (Galaxy Training Materials). https://training.galaxyproject.org/training-material/topics/epigenetics/tutorials/atac-seq/tutorial.html Online; accessed TODAY